In [120]:
import geopandas as gpd
import pandas as pd
import numpy as np
import json
import h3
import folium
import osmnx as ox
from shapely import wkt
from folium.plugins import HeatMap
from shapely.geometry import Polygon

In [121]:
m = folium.Map(location=[55.753220, 37.622513], tiles = 'openstreetmap')

def visualize_hexagons(hexagons, color="red", folium_map=m):

    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
        
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
  
# h3_address = h3.geo_to_h3(55.753605, 37.621094,  9) # 9 - индекс, определяющий размер гексагона                                                                                                     
# visualize_hexagons([h3_address])

m

In [122]:
def visualize_polygons(m, geometry):
    
    lats, lons = get_lat_lon(geometry)
    
#     m = folium.Map(location=[sum(lats)/len(lats), sum(lons)/len(lons)], zoom_start=13, tiles='cartodbpositron')
    
    overlay = gpd.GeoSeries(geometry).to_json()
    folium.GeoJson(overlay, name = 'boundary').add_to(m)
    
    return m

# выводим центроиды полигонов
def get_lat_lon(geometry):
        
    lon = geometry.apply(lambda x: x.x if x.type == 'Point' else x.centroid.x)
    lat = geometry.apply(lambda x: x.y if x.type == 'Point' else x.centroid.y)
    return lat, lon
  
# выгрузим границы Москвы из OSM
# cities = ['Москва']
# polygon_krd = ox.geometries_from_place(cities, {'boundary':'administrative'}).reset_index()
# polygon_krd = polygon_krd[(polygon_krd['name'] == 'Москва')]
polygon_krd = ox.geocode_to_gdf('Moscow')
# polygon_krd
# посмотрим что получилось
visualize_polygons(m, polygon_krd['geometry'])

In [123]:
def create_hexagons(m, geoJson, hexagons):
    
    polyline = geoJson['coordinates'][0]

    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
#     m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
#     my_PolyLine=folium.PolyLine(locations=polyline,weight=0,color="white")
#     m.add_child(my_PolyLine)

    hexagons = list(h3.polyfill(geoJson, hexagons))
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=3,color='blue')
#         m.add_child(my_PolyLine)
        
    polylines_x = []
    for j in range(len(polylines)):
        a = np.column_stack((np.array(polylines[j])[:,1],np.array(polylines[j])[:,0])).tolist()
        polylines_x.append([(a[i][0], a[i][1]) for i in range(len(a))])
        
    polygons_hex = pd.Series(polylines_x).apply(lambda x: Polygon(x))
        
    return polygons_hex, polylines
# polygon_hex , polylines - геометрии гексагонов в разных форматах

geoJson = json.loads(gpd.GeoSeries(polygon_krd['geometry']).to_json())
geoJson
get_coord = geoJson['features'][0]['geometry']['coordinates']
get_coord
coordinates = []
for i in get_coord:
    for j in i[0]:
        if len(j) > 1:
            j[0], j[1] = j[1], j[0]
            coordinates.append(j)
        else:
            for first in j:
                for second in first:
                    second[0], second[1] = second[1], second[0]
                    coordinates.append(second)

geoJson = {'type':'Polygon','coordinates': [coordinates]}
geoJson
polygons, polylines = create_hexagons(m, geoJson, 8)
m

In [124]:
pricol = pd.read_csv('scl_3.csv', encoding='utf-8')
pricol

Unnamed: 0                                     name    idk  seats  \
0            49                         ГБОУ школа № 924  13171   3388   
1            50                        ГБОУ школа № 1494  12916   2551   
2            51                         ГБОУ школа № 875  13265   1429   
3            52                   ГБПОУ «Воробьевы горы»  12754   1755   
4            53                        ГБОУ школа № 1191  13060   2324   
..          ...                                      ...    ...    ...   
516         583                                ГБПОУ МИК  14488   1286   
517         585                        ГБОУ школа № 2094  13409   2523   
518         587  ГБОУ школа № 1529 имени А.С. Грибоедова  13416   1254   
519         588                               ГБПОУ МГОК  13094   1154   
520         589                        ГБОУ школа № 1253  13787   2299   

     rating                                            address  \
0         3     117405, ГОРОД МОСКВА, УЛИЦА ГАЗОПРОВОД, ДОМ 5А   
1         2    127276, ГОРОД МОСКВА, УЛИЦА МАРФИНСКАЯ Б., 1, 5   
2         3  119526, ГОРОД МОСКВА, ПРОСПЕКТ ВЕРНАДСКОГО, 10...   
3         3           119334, ГОРОД МОСКВА, УЛИЦА КОСЫГИНА, 17   
4         3    город Москва, Митинская улица, дом 48, корпус 2   
..      ...                                                ...   
516       3    121351, ГОРОД МОСКВА, УЛИЦА БОБРУЙСКАЯ, 7, -, -   
517       3  108820, ГОРОД МОСКВА, ПОСЕЛЕНИЕ МОСРЕНТГЕН, ПО...   
518       3   119034, ГОРОД МОСКВА, ПЕРЕУЛОК 2-Й ОБЫДЕНСКИЙ, 9   
519       3        125362, ГОРОД МОСКВА, УЛИЦА ВИШНЁВАЯ, ДОМ 5   
520       3  119021, ГОРОД МОСКВА, БУЛЬВАР ЗУБОВСКИЙ, ДОМ 5...   

                                   center  cell_zid  adm_zid  
0    [55.5988473830385, 37.6115289229495]     89113       62  
1    [55.8278134403085, 37.5920141226003]    118802       65  
2    [55.6614155784035, 37.4910630801931]     97413       26  
3     [55.694420174795, 37.5488373780634]    102179       47  
4    [55.8523143495765, 37.3589551806447]    121960       13  
..                                    ...       ...      ...  
516  [55.6510837828605, 37.3669406168673]     96207       11  
517   [55.612698761648, 37.4723991452014]     90880      272  
518   [55.743124351482, 37.5947421391849]    108669       50  
519   [55.829509289158, 37.4319796639785]    119315       23  
520    [55.732729672781, 37.590880133857]    106906       50  

[521 rows x 9 columns]

In [125]:

pricol_coordinates = pricol['center'].values.tolist()
pricol_coordinates
lat_coords = []
lon_coords = []
for coords in pricol_coordinates:
    coordinates = coords.split(',')
    lat_coords.append(float(coordinates[0].replace('[', '')))
    lon_coords.append(float(coordinates[1].replace(']', '')))
lat_series = pd.Series(lat_coords)
lon_series = pd.Series(lon_coords)
pricol['lat'] = lat_series
pricol['lon'] = lon_series

pricol

Unnamed: 0                                     name    idk  seats  \
0            49                         ГБОУ школа № 924  13171   3388   
1            50                        ГБОУ школа № 1494  12916   2551   
2            51                         ГБОУ школа № 875  13265   1429   
3            52                   ГБПОУ «Воробьевы горы»  12754   1755   
4            53                        ГБОУ школа № 1191  13060   2324   
..          ...                                      ...    ...    ...   
516         583                                ГБПОУ МИК  14488   1286   
517         585                        ГБОУ школа № 2094  13409   2523   
518         587  ГБОУ школа № 1529 имени А.С. Грибоедова  13416   1254   
519         588                               ГБПОУ МГОК  13094   1154   
520         589                        ГБОУ школа № 1253  13787   2299   

     rating                                            address  \
0         3     117405, ГОРОД МОСКВА, УЛИЦА ГАЗОПРОВОД, ДОМ 5А   
1         2    127276, ГОРОД МОСКВА, УЛИЦА МАРФИНСКАЯ Б., 1, 5   
2         3  119526, ГОРОД МОСКВА, ПРОСПЕКТ ВЕРНАДСКОГО, 10...   
3         3           119334, ГОРОД МОСКВА, УЛИЦА КОСЫГИНА, 17   
4         3    город Москва, Митинская улица, дом 48, корпус 2   
..      ...                                                ...   
516       3    121351, ГОРОД МОСКВА, УЛИЦА БОБРУЙСКАЯ, 7, -, -   
517       3  108820, ГОРОД МОСКВА, ПОСЕЛЕНИЕ МОСРЕНТГЕН, ПО...   
518       3   119034, ГОРОД МОСКВА, ПЕРЕУЛОК 2-Й ОБЫДЕНСКИЙ, 9   
519       3        125362, ГОРОД МОСКВА, УЛИЦА ВИШНЁВАЯ, ДОМ 5   
520       3  119021, ГОРОД МОСКВА, БУЛЬВАР ЗУБОВСКИЙ, ДОМ 5...   

                                   center  cell_zid  adm_zid        lat  \
0    [55.5988473830385, 37.6115289229495]     89113       62  55.598847   
1    [55.8278134403085, 37.5920141226003]    118802       65  55.827813   
2    [55.6614155784035, 37.4910630801931]     97413       26  55.661416   
3     [55.694420174795, 37.5488373780634]    102179       47  55.694420   
4    [55.8523143495765, 37.3589551806447]    121960       13  55.852314   
..                                    ...       ...      ...        ...   
516  [55.6510837828605, 37.3669406168673]     96207       11  55.651084   
517   [55.612698761648, 37.4723991452014]     90880      272  55.612699   
518   [55.743124351482, 37.5947421391849]    108669       50  55.743124   
519   [55.829509289158, 37.4319796639785]    119315       23  55.829509   
520    [55.732729672781, 37.590880133857]    106906       50  55.732730   

           lon  
0    37.611529  
1    37.592014  
2    37.491063  
3    37.548837  
4    37.358955  
..         ...  
516  37.366941  
517  37.472399  
518  37.594742  
519  37.431980  
520  37.590880  

[521 rows x 11 columns]

In [126]:
gdf_1 = gpd.GeoDataFrame(pricol, geometry=gpd.points_from_xy(pricol.lon, pricol.lat))
gdf_2 = pd.DataFrame(polygons, columns = ['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)
gdf_2 = gdf_2.merge(geometry_uniq, on = 'geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')
itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
itog_table = itog_table.dropna()
itog_table

C:\conda\lib\site-packages\IPython\core\interactiveshell.py:3357: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


geometry  \
7     POLYGON ((37.50118 55.79550, 37.50466 55.79989...   
7     POLYGON ((37.50118 55.79550, 37.50466 55.79989...   
8     POLYGON ((37.57586 55.80414, 37.57144 55.80806...   
18    POLYGON ((37.60459 55.86862, 37.61252 55.86909...   
19    POLYGON ((37.57803 55.89214, 37.58596 55.89262...   
...                                                 ...   
1470  POLYGON ((37.87782 55.73791, 37.88135 55.74230...   
1473  POLYGON ((37.67428 55.85180, 37.67870 55.84787...   
1476  POLYGON ((37.82594 55.81454, 37.83388 55.81499...   
1478  POLYGON ((37.45912 55.78041, 37.46702 55.78089...   
1478  POLYGON ((37.45912 55.78041, 37.46702 55.78089...   

                                              polylines    id  index_right  \
7     [(55.79549551236043, 37.501175726543835), (55....     7        427.0   
7     [(55.79549551236043, 37.501175726543835), (55....     7        403.0   
8     [(55.804137119258854, 37.575859924389015), (55...     8        151.0   
18    [(55.86861599567698, 37.604589241706286), (55....    18        266.0   
19    [(55.89214422989072, 37.578029462792124), (55....    19        497.0   
...                                                 ...   ...          ...   
1470  [(55.73790968751934, 37.877822339965945), (55....  1470        262.0   
1473  [(55.851799735994035, 37.674276891073006), (55...  1473        123.0   
1476  [(55.81453766879009, 37.82594207088968), (55.8...  1476        377.0   
1478  [(55.78041347802684, 37.459119145761065), (55....  1478        290.0   
1478  [(55.78041347802684, 37.459119145761065), (55....  1478        302.0   

      Unnamed: 0                        name      idk   seats  rating  \
7          489.0  ГБОУ «Школа № 1212 Щукино»  14247.0  1087.0     3.0   
7          465.0            ГБОУ школа № 149  13354.0   397.0     3.0   
8          205.0           ГБОУ школа № 1601  13880.0  1572.0     3.0   
18         325.0           ГБОУ школа № 1411  13746.0  3252.0     3.0   
19         562.0           ГБОУ школа № 1416  13816.0  1504.0     3.0   
...          ...                         ...      ...     ...     ...   
1470       321.0           ГБОУ школа № 1591  13661.0  3222.0     2.0   
1473       177.0           ГБОУ школа № 1577  14451.0  1419.0     3.0   
1476       439.0           ГБОУ школа № 1516  13919.0  1364.0     2.0   
1478       349.0            ГБОУ школа № 138  13785.0  2458.0     3.0   
1478       361.0       ГБПОУ колледж полиции  11658.0   195.0     3.0   

                                                address  \
7     123060, ГОРОД МОСКВА, УЛИЦА МАРШАЛА РЫБАЛКО, Д...   
7            125080, ГОРОД МОСКВА, УЛИЦА ВРУБЕЛЯ, ДОМ 6   
8     127220, ГОРОД МОСКВА, УЛИЦА НИЖНЯЯ МАСЛОВКА, Д...   
18           127566, ГОРОД МОСКВА, БУЛЬВАР СЕВЕРНЫЙ, 1А   
19          127576, ГОРОД МОСКВА, УЛИЦА НОВГОРОДСКАЯ, 8   
...                                                 ...   
1470  111672, ГОРОД МОСКВА, УЛИЦА НОВОКОСИНСКАЯ, ДОМ...   
1473  129337, ГОРОД МОСКВА, ШОССЕ ЯРОСЛАВСКОЕ, ДОМ 8...   
1476        107589, ГОРОД МОСКВА, УЛИЦА ХАБАРОВСКАЯ, 4А   
1478  123154, ГОРОД МОСКВА, УЛИЦА ГЕНЕРАЛА ГЛАГОЛЕВА...   
1478         125363, ГОРОД МОСКВА, УЛИЦА ФАБРИЦИУСА, 26   

                                    center  cell_zid  adm_zid        lat  \
7      [55.7995763928535, 37.489898721493]  115526.0     30.0  55.799576   
7       [55.801204582858, 37.499313476541]  115527.0     37.0  55.801205   
8      [55.800411090376, 37.5684515772125]  115536.0     55.0  55.800411   
18     [55.870893093546, 37.6023995370255]  124056.0     60.0  55.870893   
19     [55.893549252709, 37.5813414477651]  126478.0     52.0  55.893549   
...                                    ...       ...      ...        ...   
1470   [55.741815773078, 37.8724139463923]  108117.0    123.0  55.741816   
1473   [55.853434779895, 37.6887085777011]  122002.0     96.0  55.853435   
1476  [55.8167757227445, 37.8317850209982]  117755.0    116.0  55.816776   
1478   [55.782320881168, 37.4664348584209]  113267.0   

In [127]:
def create_choropleth_school(m, data, json, columns,  legend_name, feature, bins):
    
    lat, lon = get_lat_lon(data['geometry'])
#     print(lat)
#     print(type(lat))
#     m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')
    
    choropleth = folium.Choropleth(
        geo_data=json,
        name="количество учебных мест",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="Greens",
        fill_opacity=0.8,
        line_opacity=0.5,
        legend_name=legend_name,
        nan_fill_color = 'Black',
        bins = bins
    ).add_to(m)

#     folium.LayerControl().add_to(m)
    
    choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['data'], labels=False))

    return m

all_ids = itog_table['id'].values.tolist()
all_titles = itog_table['name'].values.tolist()
all_rating = itog_table['rating'].values.tolist()
all_seats = itog_table['seats'].values.tolist()

all_params = {}
for i in range(len(all_ids)):
    if all_ids[i] in all_params:
        all_params[all_ids[i]].append([all_titles[i], all_rating[i], all_seats[i]])
    else:
        all_params[all_ids[i]] = [[all_titles[i], all_rating[i], all_seats[i]]]

itog_table['geometry'] = itog_table['geometry'].astype(str)
itog_table['id'] = itog_table['id'].astype(str)
agg_all = itog_table.groupby(['geometry','id'], as_index = False).agg({'seats':'sum'})
agg_all['geometry'] = agg_all['geometry'].apply(wkt.loads) #возвращаем формат геометрий
agg_all_schools = pd.DataFrame(agg_all['geometry'])

# # print(agg_all)
agg_all_schools['counts'] = agg_all['seats']
agg_all_schools['id'] = agg_all['id'].astype(str)

data_geo_1 = gpd.GeoSeries(agg_all_schools.set_index('id')["geometry"]).to_json()


# print(data_geo_1)

# # print(agg_all_schools)

with open('geo_data_schools.txt', encoding="utf-8") as json_file:
    map_data = json_file.readlines()
    map_data = [json.loads(line) for line in map_data]
map_data = map_data[0]
print(data_geo_1)

#Копирую data_geo в файл чтобы потом добавить в этот json данные
#потом открываю файл и добавляю в json параметры

idkeys = agg_all_schools['id'].values.tolist()
# namekeys = agg_all_schools['name'].values.tolist()
# seatskeys = agg_all_schools['seats'].values.tolist()
# ratingkeys = agg_all_schools['rating'].values.tolist()

# for i in range(len(idkeys)):
#     map_data['features'][i]['properties']['data'] = {'name' : namekeys[i], 'id' : idkeys[i], 'seats' : seatskeys[i], 'rating' : ratingkeys[i]}
# print(map_data)

for i in range(len(idkeys)):
    for key in all_params:
        if idkeys[i] == key:
            map_data['features'][i]['properties']['data'] = all_params[key]

# print(map_data)
create_choropleth_school(m, agg_all_schools, map_data, ["id","counts"], 'количество учебных мест в гексагоне', 'counts', 5)
# folium.Marker(location=(float(itog_table[lat]), float(itog_table[lon])), popup = "Google HQ", icon=folium.Icon(color = 'gray')).add_to(m)
# agg_all
m

C:\conda\lib\site-packages\geopandas\geodataframe.py:1350: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


{"type": "FeatureCollection", "features": [{"id": "102", "type": "Feature", "properties": {}, "geometry": {"type": "Polygon", "coordinates": [[[37.33888051638941, 55.85675098273028], [37.3433190678628, 55.85284191704284], [37.35122506311912, 55.85332754811663], [37.35469403235738, 55.85772256736642], [37.35025561676306, 55.86163208558634], [37.34234809585392, 55.86114613199381], [37.33888051638941, 55.85675098273028]]]}, "bbox": [37.33888051638941, 55.85284191704284, 37.35469403235738, 55.86163208558634]}, {"id": "945", "type": "Feature", "properties": {}, "geometry": {"type": "Polygon", "coordinates": [[[37.34041932196597, 55.63932245646667], [37.34483438545639, 55.63540704919617], [37.35269881871781, 55.63588571080878], [37.35614969795482, 55.64028010258008], [37.3517347689996, 55.64419596227075], [37.34386882607781, 55.64371697773998], [37.34041932196597, 55.63932245646667]]]}, "bbox": [37.34041932196597, 55.63540704919617, 37.35614969795482, 55.64419596227075]}, {"id": "108", "type

In [128]:
polygons, polylines = create_hexagons(m, geoJson, 10)
pricol_novostroyki = pd.read_csv('nd_4.csv', encoding='utf-8')
pricol_novostroyki
pricol_nd_coordinates = pricol_novostroyki['coordinates'].values.tolist()
pricol_nd_coordinates
lat_coords_nd = []
lon_coords_nd = []
for coords in pricol_nd_coordinates:
    coordinates = coords.split(',')
    lat_coords_nd.append(float(coordinates[0].replace('[', '')))
    lon_coords_nd.append(float(coordinates[1].replace(']', '')))

lat_series = pd.Series(lat_coords_nd)
lon_series = pd.Series(lon_coords_nd)
pricol_novostroyki['lat'] = lat_series
pricol_novostroyki['lon'] = lon_series

pricol_novostroyki

gdf_1 = gpd.GeoDataFrame(pricol_novostroyki, geometry=gpd.points_from_xy(pricol_novostroyki.lon, pricol_novostroyki.lat))
pricol_novostroyki
gdf_2 = pd.DataFrame(polygons, columns = ['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)
gdf_2 = gdf_2.merge(geometry_uniq, on = 'geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')
itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
itog_table = itog_table.dropna()
itog_table

C:\conda\lib\site-packages\IPython\core\interactiveshell.py:3357: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


geometry  \
409    POLYGON ((37.52679 55.79524, 37.52743 55.79468...   
815    POLYGON ((37.38532 55.64743, 37.38595 55.64687...   
842    POLYGON ((37.47335 55.79024, 37.47271 55.79080...   
1394   POLYGON ((37.72275 55.71945, 37.72338 55.71889...   
1394   POLYGON ((37.72275 55.71945, 37.72338 55.71889...   
...                                                  ...   
72185  POLYGON ((37.60443 55.74125, 37.60330 55.74118...   
72217  POLYGON ((37.73640 55.66101, 37.73577 55.66157...   
72217  POLYGON ((37.73640 55.66101, 37.73577 55.66157...   
72314  POLYGON ((37.51743 55.73190, 37.51680 55.73246...   
73129  POLYGON ((37.39324 55.64253, 37.39436 55.64260...   

                                               polylines     id  index_right  \
409    [(55.79523594385704, 37.52679421707717), (55.7...    409        140.0   
815    [(55.6474307584614, 37.385317053147666), (55.6...    815        202.0   
842    [(55.790236671063525, 37.47334619458365), (55....    842        274.0   
1394   [(55.71945267580925, 37.7227508720114), (55.71...   1394        328.0   
1394   [(55.71945267580925, 37.7227508720114), (55.71...   1394        332.0   
...                                                  ...    ...          ...   
72185  [(55.74124868451793, 37.604432383162546), (55....  72185        731.0   
72217  [(55.66100817807244, 37.736398265469084), (55....  72217        213.0   
72217  [(55.66100817807244, 37.736398265469084), (55....  72217        287.0   
72314  [(55.73190145403041, 37.517429892313274), (55....  72314        617.0   
73129  [(55.64252993559699, 37.3932395152405), (55.64...  73129        203.0   

       Unnamed: 0                                              title  \
409         140.0      Жилой комплекс «Прайм Тайм» (ЖК «Прайм Тайм»)   
815         202.0                   Жилой комплекс «ЛУЧИ», ЖК «ЛУЧИ»   
842         274.0                   Жилой квартал "Октябрьское поле"   
1394        328.0                      Жилой комплекс"Волжский парк"   
1394        332.0                      Жилой комплекс"Волжский парк"   
...           ...                                                ...   
72185       731.0                 Жилой дом с подземной автостоянкой   
72217       213.0                    Жилой комплекс"Люблинский парк"   
72217       287.0              Жилой комплекс"Светлый мир"Станция"Л"   
72314       617.0  "Victory Park Residences Виктори Парк Резиденсез"   
73129       203.0                   Жилой комплекс «ЛУЧИ», ЖК «ЛУЧИ»   

                                                 address      date_end  \
409                   улица Викторенко, корпус В, вл. 11  IV кв.  2021   
815                      г Москва, район Солнцево, вл. 6  IV кв.  2021   
842                       г Москва, район Щукино, вл. 30  IV кв.  2021   
1394         проезд 1-й Грайвороновский, д. 11, корпус 1   I кв.  2023   
1394   район Текстильщики, проезд 1-й Грайвороновский...  IV кв.  2022   
...                                                  ...           ...   
72185  г Москва, район Хамовники, пер Пожарский, вл. ...  IV кв.  2021   
72217      г Москва, улица Люблинская, корпус 25, вл. 72   I кв.  2022   
72217                улица Люблинская, корпус 26, вл. 72   I кв.  2024   
72314  г Москва, район Дорогомилово, улица Братьев Фо...  IV кв.  2023   
73129  район Солнцево, Производственная, корпус 7, вл. 6  IV кв.  2021   

              coordinates  flats_count  living_square  cell_zid  adm_zid  \
409     [55.7955, 37.528]        148.0        10635.0  114972.0     42.0   
815    [55.6474, 37.3859]        576.0        31627.0   95614.0     18.0   
842    [55.7897, 37.4729]       1127.0        62198.0  114403.0     30.0   
1394   [55.7197, 37.7232]        220.0         8902.0  105159.0    108.0   
1394   [55.7197, 37.7231]        210.0         9378.0  105159.0    108.0   
...                   ...          ...            ...       ...      ...   
72185  [55.7403, 37.6037]         20.0         3335.0  108083.0     50.0   
7221

In [129]:
def create_choropleth_nb(m, data, gjson, columns, legend_name, feature, bins):
#     print(gjson)
    lat, lon = get_lat_lon(data['geometry'])
    
#     m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')
    
    choropleth = folium.Choropleth(
        geo_data=gjson,
        name="Новостройки",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="Reds",
        fill_opacity=1,
        line_opacity=1,
        legend_name=legend_name,
        nan_fill_color = 'Black',
        bins = bins

    ).add_to(m)

#     folium.LayerControl().add_to(m)
    
    choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['all_nb'], labels=False))
    
    return m

flats = itog_table['flats_count'].values.tolist()
flats
flats = [int(float(flat)) for flat  in flats]


all_ids = itog_table['id'].values.tolist()
all_addresses = itog_table['title'].values.tolist()
all_date_end = itog_table['date_end'].values.tolist()
all_flats_count = itog_table['flats_count'].values.tolist()

all_params = {}
for i in range(len(all_ids)):
    if all_ids[i] in all_params:
        all_params[all_ids[i]].append([all_addresses[i], all_date_end[i], all_flats_count[i]])
    else:
        all_params[all_ids[i]] = [[all_addresses[i], all_date_end[i], all_flats_count[i]]]

# print(all_params)
        
itog_table['geometry'] = itog_table['geometry'].astype(str)
itog_table['id'] = itog_table['id'].astype(str)
agg_all = itog_table.groupby(['geometry', 'id'], as_index = False).agg({'flats_count':'sum'})
print(agg_all)
agg_all['geometry'] = agg_all['geometry'].apply(wkt.loads) #возвращаем формат геометрий
agg_all_nb = pd.DataFrame(agg_all['geometry'])
# flats_count = pd.Series(flats)

# print(agg_all)
agg_all_nb['counts'] = agg_all['flats_count']
# agg_all_nb['title'] = itog_table['title'].astype(str)
# print(agg_all_nb)
agg_all_nb['id'] = agg_all['id'].astype(str)
data_geo_1 = gpd.GeoSeries(agg_all_nb.set_index('id')["geometry"])

print(data_geo_1.to_json())

with open('testing_2120.txt', encoding="utf-8") as json_file:
    map_data = json_file.readlines()
    map_data = [json.loads(line) for line in map_data]
map_data = map_data[0]
# print(map_data)

idkeys = agg_all['id'].values.tolist()

for i in range(len(idkeys)):
    for key in all_params:
        if idkeys[i] == key:
            map_data['features'][i]['properties']['all_nb'] = all_params[key]
# print(map_data)
# print(type(data_geo_1))
create_choropleth_nb(m, agg_all_nb, map_data, ["id","counts"], 'количество квартир в гексагоне', 'counts', 5)
# agg_all

C:\conda\lib\site-packages\geopandas\geodataframe.py:1350: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


                                              geometry     id  flats_count
0    POLYGON ((37.34688070346936 55.80287286598126,...  59436       1056.0
1    POLYGON ((37.34878032796888 55.80119674584576,...  55901       1056.0
2    POLYGON ((37.35026489649454 55.80308028049252,...  42624       1368.0
3    POLYGON ((37.35924579940476 55.64285949963546,...  27544       1583.0
4    POLYGON ((37.37073044592613 55.86169303128549,...  25484        775.0
..                                                 ...    ...          ...
321  POLYGON ((37.93195106376036 55.70983757560034,...  58612        169.0
322  POLYGON ((37.93221237451048 55.71284529879022,...  71784        284.0
323  POLYGON ((37.93346619631623 55.71171844604727,...   5207        374.0
324  POLYGON ((37.93761073554656 55.71015509167378,...  39984        231.0
325  POLYGON ((37.93886438378275 55.70902813685749,...   8229        536.0

[326 rows x 3 columns]
{"type": "FeatureCollection", "features": [{"id": "59436", "type": "Feature"

In [130]:
pricol = pd.read_csv('scl_3.csv', encoding='utf-8')
pricol

polygons, polylines = create_hexagons(m, geoJson, 10)

In [131]:
pricol_coordinates = pricol['center'].values.tolist()
pricol_coordinates
lat_coords = []
lon_coords = []
for coords in pricol_coordinates:
    coordinates = coords.split(',')
    lat_coords.append(float(coordinates[0].replace('[', '')))
    lon_coords.append(float(coordinates[1].replace(']', '')))
lat_series = pd.Series(lat_coords)
lon_series = pd.Series(lon_coords)
pricol['lat'] = lat_series
pricol['lon'] = lon_series

pricol

Unnamed: 0                                     name    idk  seats  \
0            49                         ГБОУ школа № 924  13171   3388   
1            50                        ГБОУ школа № 1494  12916   2551   
2            51                         ГБОУ школа № 875  13265   1429   
3            52                   ГБПОУ «Воробьевы горы»  12754   1755   
4            53                        ГБОУ школа № 1191  13060   2324   
..          ...                                      ...    ...    ...   
516         583                                ГБПОУ МИК  14488   1286   
517         585                        ГБОУ школа № 2094  13409   2523   
518         587  ГБОУ школа № 1529 имени А.С. Грибоедова  13416   1254   
519         588                               ГБПОУ МГОК  13094   1154   
520         589                        ГБОУ школа № 1253  13787   2299   

     rating                                            address  \
0         3     117405, ГОРОД МОСКВА, УЛИЦА ГАЗОПРОВОД, ДОМ 5А   
1         2    127276, ГОРОД МОСКВА, УЛИЦА МАРФИНСКАЯ Б., 1, 5   
2         3  119526, ГОРОД МОСКВА, ПРОСПЕКТ ВЕРНАДСКОГО, 10...   
3         3           119334, ГОРОД МОСКВА, УЛИЦА КОСЫГИНА, 17   
4         3    город Москва, Митинская улица, дом 48, корпус 2   
..      ...                                                ...   
516       3    121351, ГОРОД МОСКВА, УЛИЦА БОБРУЙСКАЯ, 7, -, -   
517       3  108820, ГОРОД МОСКВА, ПОСЕЛЕНИЕ МОСРЕНТГЕН, ПО...   
518       3   119034, ГОРОД МОСКВА, ПЕРЕУЛОК 2-Й ОБЫДЕНСКИЙ, 9   
519       3        125362, ГОРОД МОСКВА, УЛИЦА ВИШНЁВАЯ, ДОМ 5   
520       3  119021, ГОРОД МОСКВА, БУЛЬВАР ЗУБОВСКИЙ, ДОМ 5...   

                                   center  cell_zid  adm_zid        lat  \
0    [55.5988473830385, 37.6115289229495]     89113       62  55.598847   
1    [55.8278134403085, 37.5920141226003]    118802       65  55.827813   
2    [55.6614155784035, 37.4910630801931]     97413       26  55.661416   
3     [55.694420174795, 37.5488373780634]    102179       47  55.694420   
4    [55.8523143495765, 37.3589551806447]    121960       13  55.852314   
..                                    ...       ...      ...        ...   
516  [55.6510837828605, 37.3669406168673]     96207       11  55.651084   
517   [55.612698761648, 37.4723991452014]     90880      272  55.612699   
518   [55.743124351482, 37.5947421391849]    108669       50  55.743124   
519   [55.829509289158, 37.4319796639785]    119315       23  55.829509   
520    [55.732729672781, 37.590880133857]    106906       50  55.732730   

           lon  
0    37.611529  
1    37.592014  
2    37.491063  
3    37.548837  
4    37.358955  
..         ...  
516  37.366941  
517  37.472399  
518  37.594742  
519  37.431980  
520  37.590880  

[521 rows x 11 columns]

In [132]:
gdf_1 = gpd.GeoDataFrame(pricol, geometry=gpd.points_from_xy(pricol.lon, pricol.lat))
gdf_2 = pd.DataFrame(polygons, columns = ['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)
gdf_2 = gdf_2.merge(geometry_uniq, on = 'geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')
itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
itog_table = itog_table.dropna()
itog_table

C:\conda\lib\site-packages\IPython\core\interactiveshell.py:3357: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


geometry  \
191    POLYGON ((37.66717 55.79158, 37.66780 55.79102...   
410    POLYGON ((37.36106 55.63699, 37.36155 55.63762...   
493    POLYGON ((37.63167 55.80385, 37.63230 55.80329...   
692    POLYGON ((37.70392 55.77280, 37.70329 55.77336...   
749    POLYGON ((37.57045 55.66867, 37.56982 55.66923...   
...                                                  ...   
72294  POLYGON ((37.79648 55.63513, 37.79710 55.63457...   
72753  POLYGON ((37.46967 55.65251, 37.47017 55.65314...   
72893  POLYGON ((37.62429 55.82434, 37.62492 55.82378...   
73090  POLYGON ((37.68921 55.77732, 37.68971 55.77795...   
73126  POLYGON ((37.52248 55.65148, 37.52311 55.65092...   

                                               polylines     id  index_right  \
191    [(55.79158243056272, 37.667165221905606), (55....    191        356.0   
410    [(55.63699166108898, 37.36105704127598), (55.6...    410        122.0   
493    [(55.80384979053501, 37.63166822802271), (55.8...    493        352.0   
692    [(55.77279544598045, 37.70392340522644), (55.7...    692        325.0   
749    [(55.668672076394415, 37.57044986580032), (55....    749        118.0   
...                                                  ...    ...          ...   
72294  [(55.63513075052552, 37.79647688828273), (55.6...  72294        393.0   
72753  [(55.652511841679, 37.46967330456945), (55.653...  72753         54.0   
72893  [(55.824343009864236, 37.62429044535558), (55....  72893         34.0   
73090  [(55.77732082320414, 37.689205546114444), (55....  73090        251.0   
73126  [(55.65147623572795, 37.522480108836206), (55....  73126         48.0   

       Unnamed: 0                            name      idk   seats  rating  \
191         417.0  ГБОУ школа № 1282 «Сокольники»  13936.0  1688.0     3.0   
410         175.0               ГБОУ школа № 1015  12733.0  1511.0     3.0   
493         413.0               ГБОУ школа № 1531  13827.0  1087.0     3.0   
692         386.0            ГБОУ «Школа на Яузе»  13420.0  1622.0     3.0   
749         171.0               ГБОУ школа № 2115  12687.0  1706.0     3.0   
...           ...                             ...      ...     ...     ...   
72294       455.0            ГБОУ школа в Капотне  13676.0  2423.0     3.0   
72753       106.0          ГБОУ школа «Тропарево»  13907.0  1031.0     3.0   
72893        86.0   ГБОУ школа № 1415 «Останкино»  13981.0  1153.0     2.0   
73090       309.0          ГБОУ «Айти-школа МЦКО»  14052.0     1.0     3.0   
73126       100.0                ГБОУ школа № 170  12474.0  1634.0     3.0   

                                                 address  \
191         107014, ГОРОД МОСКВА, УЛИЦА БАРБОЛИНА, ДОМ 1   
410    119633, ГОРОД МОСКВА, УЛИЦА НОВОПЕРЕДЕЛКИНСКАЯ...   
493     129085, ГОРОД МОСКВА, УЛИЦА ГОДОВИКОВА, 4, СТР.3   
692    105005, ГОРОД МОСКВА, ТУПИК КОНДРАШЕВСКИЙ, ДОМ 3А   
749    117418, ГОРОД МОСКВА, УЛИЦА НОВОЧЕРЁМУШКИНСКАЯ...   
...                                                  ...   
72294  109649, ГОРОД МОСКВА, УЛИЦА 5 КВАРТАЛ КАПОТНИ, 29   
72753     119602, г. Москва, ул. Академика Анохина д. 48   
72893   129515, ГОРОД МОСКВА, УЛИЦА 1-Я ОСТАНКИНСКАЯ, 29   
73090  105318, ГОРОД МОСКВА, ПЛОЩАДЬ СЕМЁНОВСКАЯ, ДОМ...   
73126       117485, ГОРОД МОСКВА, УЛИЦА ПРОФСОЮЗНАЯ, 96Б   

                                     center  cell_zid  adm_zid        lat  \
191    [55.7910970149015, 37.6678907051484]  114427.0     92.0  55.791097   
410    [55.6377569907825, 37.3608516943077]   94423.0     11.0  55.637757   
493    [55.8037406812415, 37.6320725062651]  116095.0     70.0  55.803741   
692    [55.7728621360385, 37.7036850275543]  112160.0     85.0  55.772862   
749    [55.6687213474885, 37.5691416373655]   98611.0     49.0  55.668721   
...                                     ...       ...      ...        ...   
72294  [55.6357921387925, 37.7977186704697]   94478.0    118.0  55.635792   
72753   [55.6526097222905, 37.468727188347]   96220.0     26.0  55.652610   
72893  [55.8245

In [133]:
def create_choropleth_school_points(m, data, json, columns,  legend_name, feature, bins):
    
    lat, lon = get_lat_lon(data['geometry'])
#     print(lat)
#     print(type(lat))
#     m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')
    
    choropleth = folium.Choropleth(
        geo_data=json,
        name="школы",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="Blues",
        fill_opacity=1,
        line_opacity=1,
        legend_name=legend_name,
        nan_fill_color = 'Black',
        bins = bins
    ).add_to(m)
    folium.LayerControl().add_to(m)
    
    choropleth.geojson.add_child(
    folium.features.GeoJsonTooltip(['data'], labels=False))

    return m

all_ids = itog_table['id'].values.tolist()
all_titles = itog_table['name'].values.tolist()
all_rating = itog_table['rating'].values.tolist()
all_seats = itog_table['seats'].values.tolist()

all_params = {}
for i in range(len(all_ids)):
    if all_ids[i] in all_params:
        all_params[all_ids[i]].append([all_titles[i], all_rating[i], all_seats[i]])
    else:
        all_params[all_ids[i]] = [[all_titles[i], all_rating[i], all_seats[i]]]

itog_table['geometry'] = itog_table['geometry'].astype(str)
itog_table['id'] = itog_table['id'].astype(str)
agg_all = itog_table.groupby(['geometry','id'], as_index = False).agg({'seats':'sum'})
agg_all['geometry'] = agg_all['geometry'].apply(wkt.loads) #возвращаем формат геометрий
agg_all_schools = pd.DataFrame(agg_all['geometry'])

# # print(agg_all)
agg_all_schools['counts'] = agg_all['seats']
agg_all_schools['id'] = agg_all['id'].astype(str)

data_geo_1 = gpd.GeoSeries(agg_all_schools.set_index('id')["geometry"]).to_json()


# print(data_geo_1)

# # print(agg_all_schools)

with open('school_points.txt', encoding="utf-8") as json_file:
    map_data = json_file.readlines()
    map_data = [json.loads(line) for line in map_data]
map_data = map_data[0]
print(data_geo_1)

#Копирую data_geo в файл чтобы потом добавить в этот json данные
#потом открываю файл и добавляю в json параметры

idkeys = agg_all_schools['id'].values.tolist()
# namekeys = agg_all_schools['name'].values.tolist()
# seatskeys = agg_all_schools['seats'].values.tolist()
# ratingkeys = agg_all_schools['rating'].values.tolist()

# for i in range(len(idkeys)):
#     map_data['features'][i]['properties']['data'] = {'name' : namekeys[i], 'id' : idkeys[i], 'seats' : seatskeys[i], 'rating' : ratingkeys[i]}
# print(map_data)

for i in range(len(idkeys)):
    for key in all_params:
        if idkeys[i] == key:
            map_data['features'][i]['properties']['data'] = all_params[key]

# print(map_data)
create_choropleth_school_points(m, agg_all_schools, map_data, ["id","counts"], 'школы', 'counts', 5)
# folium.Marker(location=(float(itog_table[lat]), float(itog_table[lon])), popup = "Google HQ", icon=folium.Icon(color = 'gray')).add_to(m)
# agg_all
m

C:\conda\lib\site-packages\geopandas\geodataframe.py:1350: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


{"type": "FeatureCollection", "features": [{"id": "63626", "type": "Feature", "properties": {}, "geometry": {"type": "Polygon", "coordinates": [[[37.34373085790184, 55.64490408976973], [37.34323800899025, 55.64427630150377], [37.34386882607782, 55.64371697774], [37.34499248933587, 55.64378543300947], [37.34548536631919, 55.64441321863385], [37.34485455197328, 55.64497255163038], [37.34373085790184, 55.64490408976973]]]}, "bbox": [37.34323800899025, 55.64371697774, 37.34548536631919, 55.64497255163038]}, {"id": "26146", "type": "Feature", "properties": {}, "geometry": {"type": "Polygon", "coordinates": [[[37.34406577041459, 55.63715355630314], [37.34469647173914, 55.63659419730278], [37.34581995015201, 55.63666261302517], [37.3463127580431, 55.63729039433904], [37.34568205946022, 55.63784976257216], [37.34455855024402, 55.63778134025856], [37.34406577041459, 55.63715355630314]]]}, "bbox": [37.34406577041459, 55.63659419730278, 37.3463127580431, 55.63784976257216]}, {"id": "50700", "type